<a href="https://colab.research.google.com/github/kingslayer2274/Coursera_Capstone/blob/master/Want_to_change_cities_%3F_No_worries.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Let's say you are offered the same job in a various cities around the world , but the **problem** is you like the current life style you are living , you don't want to change that , a **solution** must be found , So you use data science and machine learning to find the similarties and diffrences between cities .

### This will not only be usuful for those who are offered jobs , but also for anyone who want to move from their current city

<hr>

# In this project we are only going to apply it on three cities around the world which is:

*   Toronto , Canda 
*   Paris , France
*   New York , USA

## which datasets can be found here:
  https://en.wikipedia.org/wiki/Arrondissements_of_Paris

  https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M

  https://cocl.us/new_york_dataset



<hr/>


##  After we create a big data set compines all of the above we now have to get the location of each neighborhood of this data set :
*  We can use Geocoder library which will give us the longitude and magnitude of the place we want 

* Now after we have the location of the every place in our data set , we can use foursquare API to provide us with a recomendation of venues near any of our data set places

* Now we can use these results from foursquare to cluster our data and find similarties






# Getting The Data

In [136]:
import pandas as pd
import numpy as np

df_paris= pd.read_html("https://en.wikipedia.org/wiki/Arrondissements_of_Paris")[2]

df_toronto = pd.read_html('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')[0]



In [137]:
import json

!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset

with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

neighborhoods_data = newyork_data['features']

# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
df_york = pd.DataFrame(columns=column_names)

for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    df_york = df_york.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

## Getting the data ready
* dealing with missing (not assigned) values 
* removing unwanted data
* making sure all data frames are the same shape with same columns 
* combine them to one big data frame
* Getting coordinates of the neighborhoods using PositionStack API

In [138]:
df_toronto.head()

Postal Code           Borough               Neighborhood
0         M1A      Not assigned               Not assigned
1         M2A      Not assigned               Not assigned
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

In [139]:
# Droping any not assigned data
df_toronto = df_toronto[df_toronto["Borough"]!="Not assigned"]
# reseting index after droping rows
df_toronto.reset_index(drop=True,inplace=True)
df_toronto.head()

Postal Code           Borough                                 Neighborhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [140]:
df_paris =df_paris[["Arrondissement (R for Right Bank, L for Left Bank)" , "Name"]]
df_paris.rename(columns={"Arrondissement (R for Right Bank, L for Left Bank)":"Borough","Name":"Neighborhood"},inplace=True)
df_paris.head()

Borough    Neighborhood
0   1st (Ier) R          Louvre
1   2nd (IIe) R          Bourse
2  3rd (IIIe) R          Temple
3   4th (IVe) R  Hôtel-de-Ville
4    5th (Ve) L        Panthéon

In [141]:
df_york.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

## Combine toronto and paris 

In [142]:
df_tor_par=df_toronto.append(df_paris)
df_tor_par.reset_index(inplace=True)

In [143]:
df_tor_par.drop("index",axis=1,inplace=True)

In [144]:
df_tor_par.head()

Postal Code           Borough                                 Neighborhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [145]:
df_tor_par.drop(df_tor_par.index[100],inplace=True)  # CAnnot be found by the api for some reason
#df_tor_par.drop("index",axis=1,inplace=True)
df_tor_par.reset_index(drop=True,inplace=True)

df_tor_par.head()

Postal Code           Borough                                 Neighborhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

### Getting the Coordinates for our cities


In [146]:
# installing the api
import requests


In [ ]:
from time import sleep 

results_lat=[]
results_lon=[]
url = "https://us1.locationiq.com/v1/search.php"


for i in range (df_tor_par.shape[0]):
 
  # here we are using the borough and the neighborhood to make sure the location is accurate 
  data = {
      'key': 'd18dc0f8aaa618',
      'q':df_tor_par["Borough"][i]+" "+df_tor_par["Neighborhood"][i],
      'format': 'json'
  }
  # In case the api didn't recognize the the borough and the neighborhood together (Which happened several times)
  data_2 = {
      'key': 'd18dc0f8aaa618',
      'q':df_tor_par["Neighborhood"][i],
      'format': 'json'
  }
  try:
    r=requests.get(url,params=data)
    
    r.raise_for_status()
    results_lon.append(r.json()[0]['lon'])
    results_lat.append(r.json()[0]['lat'])
  
  except requests.HTTPError as  exception:
    req= requests.get(url,params=data_2)
    
    results_lon.append(req.json()[0]['lon'])
    results_lat.append(req.json()[0]['lat'])
  
  

 
  sleep(2)  # the api doesnt support more than one request every two seconds





In [147]:
df_tor_par.head()

Postal Code           Borough                                 Neighborhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [ ]:
# After we get the coordinates we have to add them to the dataframe
df_tor_par["Latitude"]=results_lat
df_tor_par["Longitude"]=results_lon
#df_tor_par.drop(["level_0","index"],axis=1,inplace=True)
df_tor_par.head()

Postal Code           Borough  ...    Latitude    Longitude
0         M3A        North York  ...  43.7611243  -79.3240594
1         M4A        North York  ...   43.732658  -79.3111892
2         M5A  Downtown Toronto  ...      1.2652     103.8201
3         M6A        North York  ...  43.7227784  -79.4509332
4         M7A  Downtown Toronto  ...  -32.003661   115.944763

[5 rows x 5 columns]

### Now we finally can get the whole dataset together

In [ ]:
df_all= df_tor_par.drop("Postal Code",axis=1).append(df_york)
df_all.head()

Borough  ...    Longitude
0        North York  ...  -79.3240594
1        North York  ...  -79.3111892
2  Downtown Toronto  ...     103.8201
3        North York  ...  -79.4509332
4  Downtown Toronto  ...   115.944763

[5 rows x 4 columns]

In [ ]:

df_all.reset_index(drop=True,inplace=True)
df_all.head()

Borough  ...    Longitude
0        North York  ...  -79.3240594
1        North York  ...  -79.3111892
2  Downtown Toronto  ...     103.8201
3        North York  ...  -79.4509332
4  Downtown Toronto  ...   115.944763

[5 rows x 4 columns]

In [ ]:
latitude=43.7611243
longitude=-79.3240594

import folium
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_all['Latitude'], df_all['Longitude'], df_all['Borough'], df_all['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

### From the map we can see that our api did average work in locating the places , so we have to remove all locations that is not in our three cities

In [150]:
df_toronto_cor = df_all[(df_all["Longitude"]>-79.653266) & (df_all["Longitude"]<-79.1085)]

In [151]:
df_york_cor = df_all[(df_all["Longitude"]>-74.2765) & (df_all["Longitude"]<-73.686207)]
df_york_cor

Borough               Neighborhood   Latitude  Longitude
21            York        Caledonia-Fairbanks  41.269299 -73.775329
122          Bronx                  Wakefield  40.894705 -73.847201
123          Bronx                 Co-op City  40.874294 -73.829939
124          Bronx                Eastchester  40.887556 -73.827806
125          Bronx                  Fieldston  40.895437 -73.905643
126          Bronx                  Riverdale  40.890834 -73.912585
127          Bronx                Kingsbridge  40.881687 -73.902818
128      Manhattan                Marble Hill  40.876551 -73.910660
129          Bronx                   Woodlawn  40.898273 -73.867315
130          Bronx                    Norwood  40.877224 -73.879391
131          Bronx             Williamsbridge  40.881039 -73.857446
132          Bronx                 Baychester  40.866858 -73.835798
133          Bronx             Pelham Parkway  40.857413 -73.854756
134          Bronx                City Island  40.847247 -73.786488
135          Bronx               Bedford Park  40.870185 -73.885512
136          Bronx         University Heights  40.855727 -73.910416
137          Bronx             Morris Heights  40.847898 -73.919672
138          Bronx                    Fordham  40.860997 -73.896427
139          Bronx               East Tremont  40.842696 -73.887356
140          Bronx                 West Farms  40.839475 -73.877745
141          Bronx               High  Bridge  40.836623 -73.926102
142          Bronx                    Melrose  40.819754 -73.909422
143          Bronx                 Mott Haven  40.806239 -73.916100
144          Bronx                Port Morris  40.801664 -73.913221
145          Bronx                   Longwood  40.815099 -73.895788
146          Bronx                Hunts Point  40.809730 -73.883315
147          Bronx                 Morrisania  40.823592 -73.901506
148          Bronx                  Soundview  40.821012 -73.865746
149          Bronx               Clason Point  40.806551 -73.854144
150          Bronx                Throgs Neck  40.815109 -73.816350
151          Bronx               Country Club  40.844246 -73.824099
152          Bronx                Parkchester  40.837938 -73.856003
153          Bronx         Westchester Square  40.840619 -73.842194
154          Bronx                   Van Nest  40.843608 -73.866299
155          Bronx                Morris Park  40.847549 -73.850402
156          Bronx                    Belmont  40.857277 -73.888452
157          Bronx             Spuyten Duyvil  40.881395 -73.917190
158          Bronx            North Riverdale  40.908543 -73.904531
159          Bronx                 Pelham Bay  40.850641 -73.832074
160          Bronx              Schuylerville  40.826580 -73.826203
161          Bronx             Edgewater Park  40.821986 -73.813885
162          Bronx                Castle Hill  40.819014 -73.848027
163          Bronx                  Olinville  40.871371 -73.863324
164          Bronx             Pelham Gardens  40.862966 -73.841612
165          Bronx                  Concourse  40.834284 -73.915589
166          Bronx                  Unionport  40.829774 -73.850535
167          Bronx                   Edenwald  40.884561 -73.848083
168       Brooklyn                  Bay Ridge  40.625801 -74.030621
169       Brooklyn                Bensonhurst  40.611009 -73.995180
170       Brooklyn                Sunset Park  40.645103 -74.010316
171       Brooklyn                 Greenpoint  40.730201 -73.954241
172       Brooklyn                  Gravesend  40.595260 -73.973471
173       Brooklyn             Brighton Beach  40.576825 -73.965094
174       Brooklyn             Sheepshead Bay  40.586890 -73.943186
175       Brooklyn          Manhattan Terrace  40.614433 -73.957438
176       Brooklyn                   Flatbush  40.636326 -73.958401
177       Brooklyn              Crown Heights  40.670829 -73.943291
178       Brooklyn              East Flatbush  40.641718 -73.936103

In [152]:
df_par_cor=df_all[(df_all["Longitude"]>2.206163) & (df_all["Longitude"]<2.42054)]
df_par_cor

Borough         Neighborhood   Latitude  Longitude
102      1st (Ier) R               Louvre  48.861147   2.338028
103      2nd (IIe) R               Bourse  48.868630   2.341474
104     3rd (IIIe) R               Temple  48.866500   2.360708
105      4th (IVe) R       Hôtel-de-Ville  48.856426   2.352528
106       5th (Ve) L             Panthéon  48.846191   2.346079
107      6th (VIe) L           Luxembourg  48.845472   2.339808
108     7th (VIIe) L       Palais-Bourbon  48.861596   2.317909
110      9th (IXe) R                Opéra  48.870645   2.332330
111      10th (Xe) R             Entrepôt  48.876106   2.359910
112     11th (XIe) R           Popincourt  48.857491   2.377321
113    12th (XIIe) R              Reuilly  48.844501   2.390229
114   13th (XIIIe) L             Gobelins  48.837017   2.352253
115    14th (XIVe) L         Observatoire  48.835903   2.335747
116     15th (XVe) L            Vaugirard  48.839578   2.301292
117    16th (XVIe) R                Passy  48.857505   2.280983
118   17th (XVIIe) R  Batignolles-Monceau  48.880292   2.308593
119  18th (XVIIIe) R     Butte-Montmartre  48.886705   2.341572
120    19th (XIXe) R      Buttes-Chaumont  48.878396   2.381201
121     20th (XXe) R         Ménilmontant  48.868609   2.389824

In [153]:
df_all_cor = df_toronto_cor.append(df_york_cor)
df_all_cor=df_all_cor.append(df_par_cor)
df_all_cor.reset_index(drop=True,inplace=True)
df_all_cor

Borough  ...  Longitude
0          North York  ... -79.324059
1          North York  ... -79.311189
2          North York  ... -79.450933
3           Etobicoke  ... -79.590908
4         Scarborough  ... -79.257126
5          North York  ... -79.345944
6    Downtown Toronto  ... -79.378030
7          North York  ... -79.440685
8           Etobicoke  ... -79.547098
9          North York  ... -79.345944
10          East York  ... -79.319132
11   Downtown Toronto  ... -79.375941
12               York  ... -79.424931
13          Etobicoke  ... -79.585922
14        Scarborough  ... -79.204958
15       East Toronto  ... -79.296712
16   Downtown Toronto  ... -79.375396
17        Scarborough  ... -79.225291
18          East York  ... -79.377122
19   Downtown Toronto  ... -79.383513
20   Downtown Toronto  ... -79.381164
21        Scarborough  ... -79.226692
22         North York  ... -79.365019
23         North York  ... -79.454703
24          East York  ... -79.345407
25       West Toronto  ... -79.427410
26        Scarborough  ... -79.211632
27         North York  ... -79.337000
28         North York  ... -79.501544
29   Downtown Toronto  ... -79.381164
30        Scarborough  ... -79.260382
31         North York  ... -79.376662
32         North York  ... -79.462248
33       East Toronto  ... -79.352594
34   Downtown Toronto  ... -79.381087
35         North York  ... -79.462248
36         North York  ... -79.571760
37         North York  ... -79.425679
38         North York  ... -79.462248
39       East Toronto  ... -79.395321
40         North York  ... -79.405921
41         North York  ... -79.537142
42        Scarborough  ... -79.255686
43         North York  ... -79.413300
44         North York  ... -79.462248
45    Central Toronto  ... -79.403253
46    Central Toronto  ... -79.443641
47               York  ... -79.482108
48               York  ... -79.516247
49         North York  ... -79.406657
50    Central Toronto  ... -79.397291
51       West Toronto  ... -79.474439
52          Etobicoke  ... -79.521043
53         North York  ... -79.413300
54    Central Toronto  ... -79.403253
55       West Toronto  ... -79.451038
56          Etobicoke  ... -79.553568
57        Scarborough  ... -79.315759
58    Central Toronto  ... -79.397291
59   Downtown Toronto  ... -79.378500
60       West Toronto  ... -79.473916
61    Central Toronto  ... -79.390504
62        Scarborough  ... -79.296370
63    Central Toronto  ... -79.465400
64   Downtown Toronto  ... -79.387748
65          Etobicoke  ... -79.511589
66        Scarborough  ... -79.307979
67   Downtown Toronto  ... -79.401443
68          Etobicoke  ... -79.553007
69          Etobicoke  ... -79.588461
70        Scarborough  ... -79.184839
71   Downtown Toronto  ... -79.374263
72          Etobicoke  ... -79.590908
73   Downtown Toronto  ... -79.381087
74          Etobicoke  ... -79.503214
75               York  ... -73.775329
76              Bronx  ... -73.847201
77              Bronx  ... -73.829939
78              Bronx  ... -73.827806
79              Bronx  ... -73.905643
80              Bronx  ... -73.912585
81              Bronx  ... -73.902818
82          Manhattan  ... -73.910660
83              Bronx  ... -73.867315
84              Bronx  ... -73.879391
85              Bronx  ... -73.857446
86              Bronx  ... -73.835798
87              Bronx  ... -73.854756
88              Bronx  ... -73.786488
89              Bronx  ... -73.885512
90              Bronx  ... -73.910416
91              Bronx  ... -73.919672
92              Bronx  ... -73.896427
93              Bronx  ... -73.887356
94              Bronx  ... -73.877745
95              Bronx  ... -73.926102
96              Bronx  ... -73.909422
97              Bronx  ... -73.916100
98              Bronx  ... -73.913221
99              Bronx  ... -73.895788
100             Bronx  ... -73.883315
101             Bronx  ... -73.901506
102             Bronx  ... -73.865746
103             Bronx  ... -73.854144
104             Bronx  .

In [126]:
latitude=43.7611243
longitude=-79.3240594

import folium
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_all_cor['Latitude'], df_all_cor['Longitude'], df_all_cor['Borough'], df_all_cor['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

# Finaly we have our data ready

In [ ]:
df_par_cor
df_all_cor.reset_index(drop=True,inplace=True)

Borough         Neighborhood   Latitude  Longitude
0       1st (Ier) R               Louvre  48.861147   2.338028
1       2nd (IIe) R               Bourse  48.868630   2.341474
2      3rd (IIIe) R               Temple  48.866500   2.360708
3       4th (IVe) R       Hôtel-de-Ville  48.856426   2.352528
4        5th (Ve) L             Panthéon  48.846191   2.346079
5       6th (VIe) L           Luxembourg  48.845472   2.339808
6      7th (VIIe) L       Palais-Bourbon  48.861596   2.317909
7       9th (IXe) R                Opéra  48.870645   2.332330
8       10th (Xe) R             Entrepôt  48.876106   2.359910
9      11th (XIe) R           Popincourt  48.857491   2.377321
10    12th (XIIe) R              Reuilly  48.844501   2.390229
11   13th (XIIIe) L             Gobelins  48.837017   2.352253
12    14th (XIVe) L         Observatoire  48.835903   2.335747
13     15th (XVe) L            Vaugirard  48.839578   2.301292
14    16th (XVIe) R                Passy  48.857505   2.280983
15   17th (XVIIe) R  Batignolles-Monceau  48.880292   2.308593
16  18th (XVIIIe) R     Butte-Montmartre  48.886705   2.341572
17    19th (XIXe) R      Buttes-Chaumont  48.878396   2.381201
18     20th (XXe) R         Ménilmontant  48.868609   2.389824

In [212]:
venues_paris=[]

def foursquare_results(df_cor,venues):
  url='https://api.foursquare.com/v2/search/recommendations'
  for i in range(df_cor.shape[0]):
    params = dict(
    client_id='D5SOPIFADLQRI0ZWVRFQANCEJBMWXJOIUCLGAUNMFKAOCS0Z',
    client_secret='OH0AS0IQYQQRK5MQNC3B02X40DFRETZJWVX21TO3VN2PDKJL',
    v='20180323',
    ll=df_cor["Latitude"][i].astype('str')+","+df_cor["Longitude"][i].astype('str'),
    query='coffee',
    limit=5
    )
    try:
      r=requests.get(url,params=params)
      r.raise_for_status()
      result=r.json()['response']["group"]['results']
      for j in range(len(result)):
        venues.append([result[j]['venue']['categories'][0]['name'],result[j]['venue']['name'],result[j]['venue']['location']['lat'],result[j]['venue']['location']['lng'],df_cor['Borough'][i],df_cor["Neighborhood"][i]])
    
    except requests.HTTPError as exception:
      
        venues.append(["Not result",i])
        x=exception

In [213]:
foursquare_results(df_par_cor,venues_paris)

In [220]:
venues_toronto =[]


In [221]:
foursquare_results(df_toronto_cor,venues_toronto)

In [225]:
venues_york=[]
foursquare_results(df_york_cor,venues_york)

In [228]:
tor_fs= pd.DataFrame(venues_toronto,columns=["Category","Name","Latitude","Longitude","Borough","Neighborhood"])
par_fs= pd.DataFrame(venues_paris,columns=["Category","Name","Latitude","Longitude","Borough","Neighborhood"])
york_fs= pd.DataFrame(venues_york,columns=["Category","Name","Latitude","Longitude","Borough","Neighborhood"])

In [229]:
df_fs= tor_fs.append(par_fs)
df_fs=df_fs.append(york_fs)
df_fs

Category  ...                                       Neighborhood
0             Coffee Shop  ...                                          Parkwoods
1                    Café  ...                                          Parkwoods
2             Coffee Shop  ...                                          Parkwoods
3             Coffee Shop  ...                                          Parkwoods
4                    Café  ...                                          Parkwoods
5             Coffee Shop  ...                                   Victoria Village
6                    Café  ...                                   Victoria Village
7             Coffee Shop  ...                                   Victoria Village
8             Coffee Shop  ...                                   Victoria Village
9             Coffee Shop  ...                                   Victoria Village
10               Tea Room  ...                   Lawrence Manor, Lawrence Heights
11            Coffee Shop  ...                   Lawrence Manor, Lawrence Heights
12                   Café  ...                   Lawrence Manor, Lawrence Heights
13            Coffee Shop  ...                   Lawrence Manor, Lawrence Heights
14                   Café  ...                   Lawrence Manor, Lawrence Heights
15            Coffee Shop  ...            Islington Avenue, Humber Valley Village
16            Coffee Shop  ...            Islington Avenue, Humber Valley Village
17                   Café  ...            Islington Avenue, Humber Valley Village
18            Coffee Shop  ...            Islington Avenue, Humber Valley Village
19                   Café  ...            Islington Avenue, Humber Valley Village
20               Tea Room  ...                                     Malvern, Rouge
21            Coffee Shop  ...                                     Malvern, Rouge
22            Coffee Shop  ...                                     Malvern, Rouge
23            Coffee Shop  ...                                     Malvern, Rouge
24            Coffee Shop  ...                                     Malvern, Rouge
25               Tea Room  ...                                          Don Mills
26            Coffee Shop  ...                                          Don Mills
27            Coffee Shop  ...                                          Don Mills
28            Coffee Shop  ...                                          Don Mills
29            Coffee Shop  ...                                          Don Mills
30                   Café  ...                           Garden District, Ryerson
31               Tea Room  ...                           Garden District, Ryerson
32                   Café  ...                           Garden District, Ryerson
33                   Café  ...                           Garden District, Ryerson
34            Coffee Shop  ...                           Garden District, Ryerson
35            Coffee Shop  ...                                          Glencairn
36            Coffee Shop  ...                                          Glencairn
37                   Café  ...                                          Glencairn
38            Coffee Shop  ...                                          Glencairn
39            Coffee Shop  ...                                          Glencairn
40            Coffee Shop  ...  West Deane Park, Princess Gardens, Martin Grov...
41                   Café  ...  West Deane Park, Princess Gardens, Martin Grov...
42                   Café  ...  West Deane Park, Princess Gardens, Martin Grov...
43            Coffee Shop  ...  West Deane Park, Princess Gardens, Martin Grov...
44            Coffee Shop  ...  West Deane Park, Princess Gardens, Martin Grov...
45               Tea Room  ...                                          Don Mills
46            Coffee Shop  ...                                          Don Mills
47            Coffee Shop  ...                                          Don Mills

In [232]:
df_fs=df_fs[df_fs["Category"]!="Not result"]  # Remove Data That foursquare couldn't get for any reason 

In [234]:
df_fs.reset_index(inplace=True)

In [236]:
df_fs.drop("index",axis=1,inplace=True)
df_fs

/usr/local/lib/python3.6/dist-packages/pandas/core/frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


Category  ...                                       Neighborhood
0             Coffee Shop  ...                                          Parkwoods
1                    Café  ...                                          Parkwoods
2             Coffee Shop  ...                                          Parkwoods
3             Coffee Shop  ...                                          Parkwoods
4                    Café  ...                                          Parkwoods
5             Coffee Shop  ...                                   Victoria Village
6                    Café  ...                                   Victoria Village
7             Coffee Shop  ...                                   Victoria Village
8             Coffee Shop  ...                                   Victoria Village
9             Coffee Shop  ...                                   Victoria Village
10               Tea Room  ...                   Lawrence Manor, Lawrence Heights
11            Coffee Shop  ...                   Lawrence Manor, Lawrence Heights
12                   Café  ...                   Lawrence Manor, Lawrence Heights
13            Coffee Shop  ...                   Lawrence Manor, Lawrence Heights
14                   Café  ...                   Lawrence Manor, Lawrence Heights
15            Coffee Shop  ...            Islington Avenue, Humber Valley Village
16            Coffee Shop  ...            Islington Avenue, Humber Valley Village
17                   Café  ...            Islington Avenue, Humber Valley Village
18            Coffee Shop  ...            Islington Avenue, Humber Valley Village
19                   Café  ...            Islington Avenue, Humber Valley Village
20               Tea Room  ...                                     Malvern, Rouge
21            Coffee Shop  ...                                     Malvern, Rouge
22            Coffee Shop  ...                                     Malvern, Rouge
23            Coffee Shop  ...                                     Malvern, Rouge
24            Coffee Shop  ...                                     Malvern, Rouge
25               Tea Room  ...                                          Don Mills
26            Coffee Shop  ...                                          Don Mills
27            Coffee Shop  ...                                          Don Mills
28            Coffee Shop  ...                                          Don Mills
29            Coffee Shop  ...                                          Don Mills
30                   Café  ...                           Garden District, Ryerson
31               Tea Room  ...                           Garden District, Ryerson
32                   Café  ...                           Garden District, Ryerson
33                   Café  ...                           Garden District, Ryerson
34            Coffee Shop  ...                           Garden District, Ryerson
35            Coffee Shop  ...                                          Glencairn
36            Coffee Shop  ...                                          Glencairn
37                   Café  ...                                          Glencairn
38            Coffee Shop  ...                                          Glencairn
39            Coffee Shop  ...                                          Glencairn
40            Coffee Shop  ...  West Deane Park, Princess Gardens, Martin Grov...
41                   Café  ...  West Deane Park, Princess Gardens, Martin Grov...
42                   Café  ...  West Deane Park, Princess Gardens, Martin Grov...
43            Coffee Shop  ...  West Deane Park, Princess Gardens, Martin Grov...
44            Coffee Shop  ...  West Deane Park, Princess Gardens, Martin Grov...
45               Tea Room  ...                                          Don Mills
46            Coffee Shop  ...                                          Don Mills
47            Coffee Shop  ...                                          Don Mills

# Now After we got our foursquare results we can start modeling using kmean to get the similar places

## But first we have to get our data for modeling

In [275]:
# Turning non numeric data to dummies to be able to model it using KMeans
fs_dum = pd.get_dummies(df_fs,drop_first=True)

In [276]:
fs_dum

Latitude  Longitude  ...  Neighborhood_Woodlawn  Neighborhood_York Mills West
0    43.773219 -79.321634  ...                      0                             0
1    43.760668 -79.326368  ...                      0                             0
2    43.771568 -79.320392  ...                      0                             0
3    43.770880 -79.331775  ...                      0                             0
4    43.744456 -79.346460  ...                      0                             0
5    43.723399 -79.302647  ...                      0                             0
6    43.734400 -79.345204  ...                      0                             0
7    43.735764 -79.344156  ...                      0                             0
8    43.741579 -79.318966  ...                      0                             0
9    43.725517 -79.313103  ...                      0                             0
10   43.724168 -79.453935  ...                      0                             0
11   43.725278 -79.449666  ...                      0                             0
12   43.726300 -79.452264  ...                      0                             0
13   43.725670 -79.452168  ...                      0                             0
14   43.732338 -79.455515  ...                      0                             0
15   43.644705 -79.567659  ...                      0                             0
16   43.612016 -79.578583  ...                      0                             0
17   43.631744 -79.552230  ...                      0                             0
18   43.641312 -79.576924  ...                      0                             0
19   43.627425 -79.627279  ...                      0                             0
20   43.776320 -79.258688  ...                      0                             0
21   43.766015 -79.271084  ...                      0                             0
22   43.775992 -79.232135  ...                      0                             0
23   43.785637 -79.279215  ...                      0                             0
24   43.783742 -79.253186  ...                      0                             0
25   43.777593 -79.345089  ...                      0                             0
26   43.777700 -79.344652  ...                      0                             0
27   43.773219 -79.321634  ...                      0                             0
28   43.770880 -79.331775  ...                      0                             0
29   43.792905 -79.354490  ...                      0                             0
30   43.657772 -79.376073  ...                      0                             0
31   43.656973 -79.381040  ...                      0                             0
32   43.658078 -79.378315  ...                      0                             0
33   43.657029 -79.381385  ...                      0                             0
34   43.658833 -79.383684  ...                      0                             0
35   43.700598 -79.427433  ...                      0                             0
36   43.699807 -79.461804  ...                      0                             0
37   43.703478 -79.414311  ...                      0                             0
38   43.703529 -79.413698  ...                      0                             0
39   43.713216 -79.431995  ...                      0                             0
40   43.638135 -79.537814  ...                      0                             0
41   43.631744 -79.552230  ...                      0                             0
42   43.662461 -79.532054  ...                      0                             0
43   43.644705 -79.567659  ...                      0                             0
44   43.640187 -79.538053  ...                      0                             0
45   43.777593 -79.345089  ...                      0                             0
46   43.777700 -79.344652  ...                      0     

In [281]:
# Now we train our model to get our clusters

from sklearn.cluster import KMeans
np.random.seed(42)
model = KMeans(n_clusters=5)
model.fit(fs_dum.drop(["Latitude","Longitude"],axis=1))
model.labels_[:10]

array([1, 2, 1, 1, 2, 1, 2, 1, 1, 1], dtype=int32)

In [283]:
# Now we add our clusters labels to our data frame
df_fs["Cluster Labels"]=model.labels_

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [284]:
df_fs.head()

Category                Name  ...  Neighborhood  Cluster Labels
0  Coffee Shop           Starbucks  ...     Parkwoods               1
1         Café         Tim Hortons  ...     Parkwoods               2
2  Coffee Shop         Tim Hortons  ...     Parkwoods               1
3  Coffee Shop  Aroma Espresso Bar  ...     Parkwoods               1
4         Café       Baretto Caffé  ...     Parkwoods               2

[5 rows x 7 columns]

In [294]:
import matplotlib.cm as cm
import matplotlib.colors as colors
# create map
map_clusters = folium.Map(location=[43.773219, -79.321634], zoom_start=1)

# set color scheme for the clusters
x = np.arange(5)
ys = [i + x + (i*x)**2 for i in range(5)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster ,name in zip(df_fs['Latitude'], df_fs['Longitude'], df_fs['Neighborhood'], df_fs['Cluster Labels'],df_fs['Name']):
    label = folium.Popup(str(poi) + '\n Cluster ' + str(cluster) +"\nName"+ str(name), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# No we reached the end of our journey so you can travel as you like between these three cities because you don't like change 